In [2]:
# Cell 1
import MetaTrader5 as mt5
from datetime import datetime, timedelta
from IPython.display import display
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd
import numpy as np

# for jupyt notebooks
import os
d = os.path.dirname(os.path.dirname(os.getcwd()))
print(d)
import sys
sys.path.append(d)
from mt5_trade_utils.backtester import Backtester, get_ohlc_history

# Initialize MT5
mt5.initialize()

c:\Users\derne\OneDrive - The Pennsylvania State University\Programming\Extra\algobot\ATJ


True

In [3]:
# Get historical data
symbol = 'USTECm'
start_dt = datetime(2021, 1, 1)
end_dt = datetime.now()

ohlc = get_ohlc_history(symbol, mt5.TIMEFRAME_H1, start_dt, end_dt)

# Data preprocessing
ohlc['date'] = pd.to_datetime(ohlc['time'])
ohlc['range'] = ohlc['high'] - ohlc['low']
ohlc['range_rel'] = ohlc['range'] / ohlc['open']
ohlc['hour'] = ohlc['date'].dt.hour

# Ensure data is sorted by date
ohlc = ohlc.sort_values('date')

display(ohlc.head())

time      open      high       low     close  \
0 2021-01-03 23:00:00  12897.53  12897.53  12862.52  12874.14   
1 2021-01-04 00:00:00  12874.64  12876.11  12835.25  12844.38   
2 2021-01-04 01:00:00  12844.39  12862.50  12844.39  12861.30   
3 2021-01-04 02:00:00  12861.88  12876.68  12861.80  12870.17   
4 2021-01-04 03:00:00  12870.38  12884.54  12867.02  12881.78   

                 date  range  range_rel  hour  
0 2021-01-03 23:00:00  35.01   0.002714    23  
1 2021-01-04 00:00:00  40.86   0.003174     0  
2 2021-01-04 01:00:00  18.11   0.001410     1  
3 2021-01-04 02:00:00  14.88   0.001157     2  
4 2021-01-04 03:00:00  17.52   0.001361     3

In [4]:
# Cell 3
# Calculate EMA
def calculate_ema(data, period, column='close'):
    return data[column].ewm(span=period, adjust=False).mean()

ohlc['ema_20'] = calculate_ema(ohlc, 20)
ohlc['ema_50'] = calculate_ema(ohlc, 50)

# Define candle types
def analyze_candle(x):
    if x['close'] > x['open']:
        return 'bullish candle'
    elif x['close'] < x['open']:
        return 'bearish candle'
    return 'doji'

ohlc['candle_type'] = ohlc.apply(analyze_candle, axis=1)

# Add previous candle information
ohlc['prev_candle_type'] = ohlc['candle_type'].shift(1)
ohlc['prev_low'] = ohlc['low'].shift(1)
ohlc['prev_high'] = ohlc['high'].shift(1)

display(ohlc.head())

time      open      high       low     close  \
0 2021-01-03 23:00:00  12897.53  12897.53  12862.52  12874.14   
1 2021-01-04 00:00:00  12874.64  12876.11  12835.25  12844.38   
2 2021-01-04 01:00:00  12844.39  12862.50  12844.39  12861.30   
3 2021-01-04 02:00:00  12861.88  12876.68  12861.80  12870.17   
4 2021-01-04 03:00:00  12870.38  12884.54  12867.02  12881.78   

                 date  range  range_rel  hour        ema_20        ema_50  \
0 2021-01-03 23:00:00  35.01   0.002714    23  12874.140000  12874.140000   
1 2021-01-04 00:00:00  40.86   0.003174     0  12871.305714  12872.972941   
2 2021-01-04 01:00:00  18.11   0.001410     1  12870.352789  12872.515179   
3 2021-01-04 02:00:00  14.88   0.001157     2  12870.335381  12872.423211   
4 2021-01-04 03:00:00  17.52   0.001361     3  12871.425344  12872.790144   

      candle_type prev_candle_type  prev_low  prev_high  
0  bearish candle             None       NaN        NaN  
1  bearish candle   bearish candle  12862.52   12897.53  
2  bullish candle   bearish candle  12835.25   12876.11  
3  bullish candle   bullish candle  12844.39   12862.50  
4  bullish candle   bullish candle  12861.80   12876.68

## Define trading signals

- Enters a long position at 5pm (17:00) if the previous candle was bullish and the close price is above the 20-period EMA, and the 20-period EMA is above the 50-period EMA.
- Enters a short position at 5pm (17:00) if the previous candle was bearish and the close price is below the 20-period EMA, and the 20-period EMA is below the 50-period EMA.
- Closes the position at 10pm (22:00)

In [6]:

# Define trading signals
def get_signal(x):
    if (x['prev_candle_type'] == 'bullish candle' and 
        x['hour'] == 17 and 
        x['close'] > x['ema_20'] and 
        x['ema_20'] > x['ema_50']):
        return 'buy'
    elif (x['prev_candle_type'] == 'bearish candle' and 
          x['hour'] == 17 and 
          x['close'] < x['ema_20'] and 
          x['ema_20'] < x['ema_50']):
        return 'sell'
    return None

def get_exit_signal(x):
    if x['hour'] == 22:
        return 'close'
    return None

ohlc['signal'] = ohlc.apply(get_signal, axis=1)
ohlc['exit_signal'] = ohlc.apply(get_exit_signal, axis=1)

display(ohlc[ohlc['signal'].notnull()].head())

time      open      high       low     close  \
18  2021-01-04 17:00:00  12645.77  12660.49  12533.09  12607.40   
106 2021-01-08 17:00:00  13044.76  13077.20  13021.35  13045.29   
150 2021-01-12 17:00:00  12880.21  12884.66  12780.03  12858.36   
257 2021-01-19 17:00:00  12914.19  12970.36  12909.82  12968.73   
279 2021-01-20 17:00:00  13263.25  13288.33  13256.19  13281.34   

                   date   range  range_rel  hour        ema_20        ema_50  \
18  2021-01-04 17:00:00  127.40   0.010075    17  12849.499483  12868.550539   
106 2021-01-08 17:00:00   55.85   0.004281    17  12978.575847  12887.752380   
150 2021-01-12 17:00:00  104.63   0.008123    17  12929.173151  12945.398829   
257 2021-01-19 17:00:00   60.54   0.004688    17  12906.775372  12888.507330   
279 2021-01-20 17:00:00   32.14   0.002423    17  13117.520365  13021.607732   

        candle_type prev_candle_type  prev_low  prev_high signal exit_signal  
18   bearish candle   bearish candle  12646.47   12792.40   sell        None  
106  bullish candle   bullish candle  13011.71   13069.48    buy        None  
150  bearish candle   bearish candle  12864.67   12938.17   sell        None  
257  bullish candle   bullish candle  12862.61   12919.97    buy        None  
279  bullish candle   bullish candle  13219.78   13268.43    buy        None

## Trading logic

- Enters a long position at the current open price if the signal is 'buy' and there are no open trades, with a stop loss and take profit price calculated based on the current open price and the 20-period EMA.
- Enters a short position at the current open price if the signal is 'sell' and there are no open trades, with a stop loss and take profit price calculated based on the current open price and the 20-period EMA.
- Closes the trade if the exit_signal is 'close'.
- Trails the stop loss of the trade based on the 20-period EMA, adjusting the stop loss if the EMA moves beyond the current stop loss.


In [8]:
# Trading logic
def on_bar(data, trades, orders):
    volume = 10000 / data['open']
    
    open_trades = trades[trades['state'] == 'open']
    num_open_trades = open_trades.shape[0]
    
    # Entry signal
    if data['signal'] == 'buy' and not num_open_trades:
        sl = min(data['prev_low'], data['ema_20']) # Use EMA as dynamic SL
        tp = data['open'] + 2 * (data['open'] - sl) # 1:2 risk-reward ratio
        orders.open_trade(symbol, volume, 'buy', sl=sl, tp=tp)
    
    elif data['signal'] == 'sell' and not num_open_trades:
        sl = max(data['prev_high'], data['ema_20']) # Use EMA as dynamic SL
        tp = data['open'] - 2 * (sl - data['open']) # 1:2 risk-reward ratio
        orders.open_trade(symbol, volume, 'sell', sl=sl, tp=tp)
        
    # Exit signal / trail SL
    if num_open_trades:
        trade = open_trades.iloc[0]
        
        # Exit signal
        if data['exit_signal'] == 'close':
            orders.close_trade(trade)

        # Trail stop loss
        if trade['order_type'] == 'buy':
            new_sl = max(trade['sl'], data['ema_20'])
            if new_sl > trade['sl']:
                orders.modify_sl(trade, sl=new_sl)
        elif trade['order_type'] == 'sell':
            new_sl = min(trade['sl'], data['ema_20'])
            if new_sl < trade['sl']:
                orders.modify_sl(trade, sl=new_sl)

## Backtest

In [9]:
# Backtest parameters
starting_balance = 1000
currency = 'USD'
exchange_rate = 1 
commission = -2

# Run backtest
bt = Backtester()
bt.set_starting_balance(starting_balance, currency=currency)
bt.set_exchange_rate(exchange_rate)
bt.set_commission(commission)

bt.set_historical_data(ohlc)
bt.set_on_bar(on_bar)

bt.run_backtest()

# Prepare trade data for evaluation
trades_df = bt.trades.copy()
trades_df['close_time'] = pd.to_datetime(trades_df['close_time'])
trades_df['open_time'] = pd.to_datetime(trades_df['open_time'])
trades_df['profit_cumulative'] = trades_df['profit'].cumsum()
trades_df['current_max'] = trades_df['profit_cumulative'].cummax()
trades_df['drawdown'] = trades_df['profit_cumulative'] - trades_df['current_max']

# Display trade summary
print(trades_df[['close_time', 'profit', 'profit_cumulative', 'current_max', 'drawdown']].describe())

# Custom evaluation function
def custom_evaluate_backtest(df):
    total_trades = len(df)
    winning_trades = len(df[df['profit'] > 0])
    losing_trades = len(df[df['profit'] < 0])
    win_rate = winning_trades / total_trades if total_trades > 0 else 0
    total_profit = df['profit'].sum()
    max_drawdown = df['drawdown'].min()
    
    return {
        'Total Trades': total_trades,
        'Winning Trades': winning_trades,
        'Losing Trades': losing_trades,
        'Win Rate': f'{win_rate:.2%}',
        'Total Profit': f'{total_profit:.2f}',
        'Max Drawdown': f'{max_drawdown:.2f}'
    }

# Evaluate results
evaluation = custom_evaluate_backtest(trades_df)
for key, value in evaluation.items():
    print(f'{key}: {value}')

                          close_time      profit  profit_cumulative  \
count                            432  432.000000         432.000000   
mean   2023-01-03 21:24:10.000000256    2.325903         353.906273   
min              2021-01-05 11:00:00 -290.630000        -225.330000   
25%              2021-12-08 16:45:00  -35.300000         212.417500   
50%              2022-12-25 23:00:00   -2.450000         291.475000   
75%              2024-01-25 06:30:00   35.035000         483.982500   
max              2025-01-23 19:00:00  244.280000        1105.560000   
std                              NaN   64.274195         252.231960   

       current_max    drawdown  
count   432.000000  432.000000  
mean    797.107685 -443.201412  
min     -67.550000 -953.230000  
25%     676.290000 -701.952500  
50%     957.610000 -481.505000  
75%     957.610000 -159.102500  
max    1105.560000    0.000000  
std     217.195599  288.249480  
Total Trades: 432
Winning Trades: 207
Losing Trades: 225
Win Ra

# Visualization

In [10]:
# Visualization
fig = make_subplots(rows=5, cols=1, shared_xaxes=True, vertical_spacing=0.05,
                    subplot_titles=('Market Data & Trades', 'Individual Trades', 'Cumulative Profit', 'Drawdown', 'Trade Profit Distribution'))

# 1. Candlestick chart with EMAs
fig.add_trace(go.Candlestick(x=ohlc['date'],
                             open=ohlc['open'],
                             high=ohlc['high'],
                             low=ohlc['low'],
                             close=ohlc['close'],
                             name='Candlesticks'),
              row=1, col=1)

fig.add_trace(go.Scatter(x=ohlc['date'], y=ohlc['ema_20'], name='EMA 20', line=dict(color='blue')), row=1, col=1)
fig.add_trace(go.Scatter(x=ohlc['date'], y=ohlc['ema_50'], name='EMA 50', line=dict(color='orange')), row=1, col=1)

# 2. Individual Trades
for i, trade in trades_df.iterrows():
    color = 'green' if trade['profit'] > 0 else 'red'
    fig.add_trace(go.Scatter(x=[trade['open_time'], trade['close_time']], 
                             y=[trade['open_price'], trade['close_price']],
                             mode='lines+markers',
                             line=dict(color=color),
                             name=f'Trade {i}',
                             showlegend=False),
                  row=2, col=1)

# 3. Cumulative Profit
fig.add_trace(go.Scatter(x=trades_df['close_time'], y=trades_df['profit_cumulative'],
                         mode='lines', name='Cumulative Profit'), row=3, col=1)

# 4. Drawdown
fig.add_trace(go.Scatter(x=trades_df['close_time'], y=trades_df['drawdown'],
                         mode='lines', name='Drawdown'), row=4, col=1)

# 5. Trade Profit Distribution
fig.add_trace(go.Histogram(x=trades_df['profit'], nbinsx=50, name='Profit Distribution'), row=5, col=1)

# Update layout
fig.update_layout(height=2000, title_text="Backtest Results")

# Update y-axes
fig.update_yaxes(title_text="Price", row=1, col=1)
fig.update_yaxes(title_text="Price", row=2, col=1)
fig.update_yaxes(title_text="Profit ($)", row=3, col=1)
fig.update_yaxes(title_text="Drawdown ($)", row=4, col=1)
fig.update_yaxes(title_text="Frequency", row=5, col=1)

# Update x-axes
fig.update_xaxes(title_text="Date", row=5, col=1)
fig.update_xaxes(rangeslider_visible=False, row=1, col=1)

# Ensure proper time range is displayed
fig.update_xaxes(range=[ohlc['date'].min(), ohlc['date'].max()])

fig.show()

In [11]:
fig = bt.visualize_backtest(num_trades=100)
fig